# Project Work - Data Extraction, Cleaning, and Transformation

In questo notebook, eseguiremo l'estrazione, la pulizia e la trasformazione dei datasets in formato JSON scaricati da [Kaggle](https://www.kaggle.com/datasets/thoughtvector/podcastreviews/data?select=podcasts.json) al fine di sviluppare una web app per i Podcast.
I file che utilizzeremo sono:


*   **podcasts.json**
*   **categories.json**
*   **reviews.json**


L'obiettivo è convertire questi file in un formato CSV pulito, in modo da poter inserire poi dati sul database MySql.

## Obiettivi del Notebook
1. **Caricamento dei dati JSON**: Importare i file JSON scaricati da Kaggle.
2. **Ispezione dei dati**: Analizzare la struttura dei dati per identificare eventuali problemi.
3. **Pulizia dei dati**: Gestire i valori mancanti, correggere i tipi di dati e rimuovere duplicati e incongruenze.
4. **Estrazione dati aggiuntivi**: Recupero dal web delle immagini non presenti nei file di partenza.
5. **Trasformazione dei dati**: Convertire le strutture JSON annidate in un formato tabellare.
6. **Esportazione dei dati**: Salvare i dati puliti e trasformati in file CSV pronti per l'inserimento nel database MySQL.

## Podcast JSON Cleaning and Transformation


In questa parte, caricheremo il file json relativo ai dati sui **podcast** e procederemo con i vari step.
Nella seguente cella importiamo le librerie necessarie e le funzioni per la data cleaning di questo file.

In [51]:
## librerie

import pandas as pd
import numpy as np

### funzioni per la pulizia

#a) funzione per la pulizia della colonna ratings_count

def clean_ratings_count(string):
    if pd.isna(string):
        return np.nan
    elif 'K' in string:
        return int(float(string.replace('K', '')) * 1000)
    else:
        return int(string)

#b) funzioni per la pulizia della colonna autori

def author_clean(testo, n=4):

    # mantiene solo la parte prima del primo `:`
    testo = testo.split(':', 1)[0].strip()
    lista = testo.split(', ')

    # se ci sono più di n autori, mantiene solo i primi n
    if len(lista) > n:
        return ', '.join(lista[0:n])
    else:
        return testo

def rimuovi_mail(testo):
    parole = testo.split()
    risultato = []

    for parola in parole:
        if '@' not in parola:
            risultato.append(parola)

    return ' '.join(risultato).strip()


def rimuovi_http(testo):
        return testo.replace("http://", "")


def rimuovi_http2(testo):
        return testo.replace("http", "")


def replace_long_description_with_nan(authors):
    words = authors.split()
    # se ci sono più di 8 parole, sostituisci con NaN
    if len(words) > 9:
        return np.nan
    return authors

def replace_separator(author):
    if pd.isna(author):
        return author  # mantiene i nan
    elif ';' in author:
        return author.replace(';', ',')
    elif ', and' in author:
        return author.replace(', and', ',')
    else:
        return author

In [52]:
df = pd.read_json('podcasts.json', lines=True)

In [53]:
df

podcast_id   itunes_id  \
0        d3997f1089be9e45fda4113be39765cb  1000000618   
1        f201172864310534ae6b6c4f8ae9b8cc  1000016089   
2        4e5ce6a47e5d491aac3f588cfb3ece73  1000016800   
3        6c476d3dd90c3fe5381153354b326952  1000035657   
4        b9e7fdf5cd545fc8097055e2f2f1d760  1000035702   
...                                   ...         ...   
2077660  bc746cf4f5e78ed7880f964fcebcbe4d   999969174   
2077661  c16669b79e093e976b83a8e61270a903   999971688   
2077662  b863eaa678d3de4f5721a7492fd32b3e   999975096   
2077663  920de5c8d1bb6b3fea7d86ac39473d76   999987741   
2077664  14d322aec25449b845c15dbfb46b4a6a   999992080   

                                        slug  \
0         christianity-questions-and-answers   
1                        rahdo-talks-through   
2        st-neots-evangelical-church-sermons   
3                             idiotspeakshow   
4                    conciertos-en-el-living   
...                                      ...   
2077660                        smarketsights   
2077661                save-to-the-uttermost   
2077662                    the-skift-podcast   
2077663                history-of-the-batman   
2077664                  speech-prof-podcast   

                                                itunes_url  \
0        https://podcasts.apple.com/us/podcast/christia...   
1        https://podcasts.apple.com/us/podcast/rahdo-ta...   
2        https://podcasts.apple.com/us/podcast/st-neots...   
3        https://podcasts.apple.com/us/podcast/idiotspe...   
4        https://podcasts.apple.com/us/podcast/conciert...   
...                                                    ...   
2077660  https://podcasts.apple.com/us/podcast/smarkets...   
2077661  https://podcasts.apple.com/us/podcast/save-to-...   
2077662  https://podcasts.apple.com/us/podcast/the-skif...   
2077663  https://podcasts.apple.com/us/podcast/history-...   
2077664  https://podcasts.apple.com/us/podcast/speech-p...   

                       title                             author  \
0                       None                               None   
1        Rahdo Talks Through  noreply@blogger.com (Richard Ham)   
2                       None                               None   
3             IdiotSpeakShow                     IdiotSpeakShow   
4                       None                               None   
...                      ...                                ...   
2077660                 None                               None   
2077661                 None                               None   
2077662    The Skift Podcast                              Skift   
2077663                 None                               None   
2077664                 None                               None   

                                               description  average_rating  \
0                                                     None             NaN   
1        Richard "Rahdo" Ham talks (at great length) al...             4.6   
2                                                     None             NaN   
3                                Podcast by IdiotSpeakShow             NaN   
4                                                     None             NaN   
...                                                    ...             ...   
2077660                                               None             NaN   
2077661                                               None             NaN   
2077662  Skift editors sit down with creatives, executi...             4.5   
2077663                                               None             NaN   
2077664                                               None             NaN   

        ratings_count                 scraped_at  
0                None                        NaT  
1                  60 2019-07-08 06:15:45.106345  
2                None                        NaT  
3                None 2019-07-08 06:01:23.683147  
4                None      

Dopo aver letto il file e trasfromato in dataframe, rimuoviamo le righe per quei podcast che non hanno un titolo e le colonne che non sono importanti per i nostri scopi.

In [54]:
df.dropna(subset=['title'], inplace=True)

In [55]:
df_podcast = df.drop(columns=['itunes_id', 'slug', 'scraped_at'])

In [56]:
df_podcast.info()

<class 'pandas.core.frame.DataFrame'>
Index: 153821 entries, 1 to 2077662
Data columns (total 7 columns):
 #   Column          Non-Null Count   Dtype  
---  ------          --------------   -----  
 0   podcast_id      153821 non-null  object 
 1   itunes_url      153821 non-null  object 
 2   title           153821 non-null  object 
 3   author          153821 non-null  object 
 4   description     149808 non-null  object 
 5   average_rating  82988 non-null   float64
 6   ratings_count   82988 non-null   object 
dtypes: float64(1), object(6)
memory usage: 9.4+ MB


Adesso analizziamo i valori unici presenti nella colonna `ratings_count`.
Qui possiamo notare che la colonna è di tipo object (stringa) poiché è presente il simbolo 'K' per rappresentare le migiliaia.

In [57]:
unique_ratings_count = df_podcast['ratings_count'].unique()
unique_ratings_count

array(['60', None, '3', '1.3K', '20', '11', '9', '7', '32', '22', '1',
       '2', '8', '4', '12', '17', '76', '26', '54', '44', '15', '5', '43',
       '6', '10', '24', '71', '1.8K', '13', '29', '42', '33', '51', '65',
       '47', '55', '19', '30', '45', '37', '4.2K', '14', '82', '23', '92',
       '40', '21', '41', '25', '28', '36', '31', '49', '58', '69', '27',
       '98', '16', '95', '38', '2.6K', '96', '73', '1.1K', '18', '78',
       '46', '66', '48', '97', '89', '52', '94', '53', '81', '1.7K',
       '1.5K', '91', '39', '56', '57', '35', '50', '68', '2.3K', '63',
       '90', '34', '59', '88', '84', '79', '3.5K', '85', '1.9K', '87',
       '72', '61', '5.7K', '86', '74', '2.7K', '1K', '77', '1.2K', '62',
       '75', '3.2K', '3.1K', '80', '1.4K', '2K', '4.6K', '83', '3.3K',
       '70', '8.9K', '67', '93', '7.4K', '1.6K', '4.7K', '2.2K', '5.5K',
       '4.4K', '8.2K', '64', '7.7K', '99', '6.6K', '6.1K', '4.9K', '8.6K',
       '6.8K', '3.9K', '3.4K', '2.9K', '3.7K', '3.8K', '6.

Iniziamo quindi col pulire questa colonna utilizzando la funzione `clean_ratings_count()`, applicandola all'intera colonna con il metodo `apply()`.

In [58]:
# applico la funzione alla colonna rating count e casto a intero
df_podcast['ratings_count'] = df_podcast['ratings_count'].apply(clean_ratings_count)
df_podcast['ratings_count'] = df_podcast['ratings_count'].astype('Int64')

In [59]:
df_podcast.info()

<class 'pandas.core.frame.DataFrame'>
Index: 153821 entries, 1 to 2077662
Data columns (total 7 columns):
 #   Column          Non-Null Count   Dtype  
---  ------          --------------   -----  
 0   podcast_id      153821 non-null  object 
 1   itunes_url      153821 non-null  object 
 2   title           153821 non-null  object 
 3   author          153821 non-null  object 
 4   description     149808 non-null  object 
 5   average_rating  82988 non-null   float64
 6   ratings_count   82988 non-null   Int64  
dtypes: Int64(1), float64(1), object(5)
memory usage: 9.5+ MB


A questo punto diamo un'occhiata alla colonna degli **autori**, visionandone gli **autori unici** presenti per iniziare la pulizia.

In [60]:
unique_authors = df_podcast['author'].unique()
unique_authors.tolist

for author in unique_authors:
    print(author)

noreply@blogger.com (Richard Ham)
IdiotSpeakShow
CityPodcast
PodcastOne
Jim Kettner, John Mihaly, and Scott Brown
Sports From Her Perspective
Kris Baker Dersch
Todd Mizener
PeloTonOfFun Podcast
astrodestinoatlanta
James Boulton
franziska.kranz@gmail.com (Franziska Kranz)
Cathy...
L/L Research
The Gluten Free Chef
BRB Dinner
Fernando Magno
Joel Lindstrom, Shawn Tabor, George Doubinski, Matthew C Anderson, Mark Smith, Scott Sewell
Harbour City Stories
Faces On The Radio
Matt Jacobs & Suvin Mehta
Next Level Rising
Fahlstaff City Council
Chris "Tapper" Welke
COGG - an Chomhairle um Oideachas Gaeltachta agus Gaelscolaíochta
Jagadeesh Nandakumar
Amanda Alexander
District Kights
Geeks and Geeklets
Shane Stacks
Paul Sian
Gary Zabinski, Frank Tourangeau
Washington Grain Commission
Ojo sobre el Cine
greenspirit
Gerren Kelsaw & Anthony Bejarano
D.A. Xavier
Crítica Americanista
Jimmy McKay, PT, DPT
Veronica G and Samuel B
Union Grove Missionary Baptist Church
WIRED
Marcello, Corey & Demetrick
Robe

Applichiamo quindi le varie funzioni create dopo aver visionato i dati presenti in `author`, creando un'altra colonna che chiamiamo `author_cleaned`:

In [61]:
df_podcast['author_cleaned'] = df_podcast['author'].apply(author_clean)

In [62]:
df_podcast['author_cleaned'] = df_podcast['author_cleaned'].apply(rimuovi_mail)


In [63]:
# qui uso una funzione lambda per strippare vari caratteri all'inizio e alla fine della stringa
df_podcast['author_cleaned']= df_podcast['author_cleaned'].apply(lambda x: x.strip(' .,()!'))

In [64]:
df_podcast['author_cleaned'] = df_podcast['author_cleaned'].apply(rimuovi_http)
df_podcast['author_cleaned'] = df_podcast['author_cleaned'].apply(rimuovi_http2)

In [65]:
df_podcast['author_cleaned'] = df_podcast['author_cleaned'].apply(replace_long_description_with_nan)

In [66]:
df_podcast['author_cleaned'] = df_podcast['author_cleaned'].apply(replace_separator)

In [67]:
# qui usiamo .replace() per sostituire gli autori 'Unknown' con NaN
df_podcast['author_cleaned'] = df_podcast['author_cleaned'].replace('Unknown', np.nan)

In [68]:
df_podcast.info()

<class 'pandas.core.frame.DataFrame'>
Index: 153821 entries, 1 to 2077662
Data columns (total 8 columns):
 #   Column          Non-Null Count   Dtype  
---  ------          --------------   -----  
 0   podcast_id      153821 non-null  object 
 1   itunes_url      153821 non-null  object 
 2   title           153821 non-null  object 
 3   author          153821 non-null  object 
 4   description     149808 non-null  object 
 5   average_rating  82988 non-null   float64
 6   ratings_count   82988 non-null   Int64  
 7   author_cleaned  150785 non-null  object 
dtypes: Int64(1), float64(1), object(6)
memory usage: 10.7+ MB


In [69]:
# con questa riga di codice droppiamo le righe che hanno NaN nella colonna author_cleaned
df_podcast = df_podcast.dropna(subset=['author_cleaned'])

In [70]:
df_podcast.info()

<class 'pandas.core.frame.DataFrame'>
Index: 150785 entries, 1 to 2077662
Data columns (total 8 columns):
 #   Column          Non-Null Count   Dtype  
---  ------          --------------   -----  
 0   podcast_id      150785 non-null  object 
 1   itunes_url      150785 non-null  object 
 2   title           150785 non-null  object 
 3   author          150785 non-null  object 
 4   description     146937 non-null  object 
 5   average_rating  81393 non-null   float64
 6   ratings_count   81393 non-null   Int64  
 7   author_cleaned  150785 non-null  object 
dtypes: Int64(1), float64(1), object(6)
memory usage: 10.5+ MB


In [71]:
# controllo finale per la presenza di eventuali duplicati nella colonna podcast_id

if df_podcast['podcast_id'].duplicated().any():
    print("Sono stati trovati duplicati nei podcast_id.")
else:
    print("Non ci sono duplicati nei podcast_id.")

Non ci sono duplicati nei podcast_id.


### Creazione tabelle utili e trasformazione in file csv

Dopo aver ultimato al meglio la pulizia dei dati, creiamo le tabelle utili per riempire il nostro database MySql, seguendo questi passaggi:

In [72]:
# step 1: Esplosione del dataset in base agli autori
df_podcast['author_cleaned'] = df_podcast['author_cleaned'].str.split(', ')
df_exploded = df_podcast.explode('author_cleaned').reset_index(drop=True)

# step 2: Creazione della tabella authors con autori unici
df_authors = df_exploded[['author_cleaned']].drop_duplicates().reset_index(drop=True)
df_authors['author_id'] = range(1, len(df_authors) + 1)

# step 3: Creazione della tabella molti a molti author_podcast
df_author_podcast = df_exploded[['podcast_id', 'author_cleaned']].merge(df_authors, on='author_cleaned', how='left')
df_author_podcast = df_author_podcast[['podcast_id', 'author_id']]

# step 4: Creazione della tabella podcast con solo id e titolo
df_podcast_table = df_podcast[['podcast_id', 'title']].drop_duplicates().reset_index(drop=True)

# step 5: Creazione della tabella dettagli_podcast con le altre info
df_dettagli_podcast = df_podcast[['podcast_id', 'itunes_url', 'description', 'average_rating', 'ratings_count']].drop_duplicates().reset_index(drop=True)
df_dettagli_podcast['itunes_img'] = ""  # colonna vuota per future immagini


Dopo aver eseguito la cella soprastante, controlliamo con il metodo `info()` le colonne e i tipi di dato per ciascuna tabella e poi trasformiamo ogni tabella nel realtivo csv.

In [73]:
df_podcast_table.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 150785 entries, 0 to 150784
Data columns (total 2 columns):
 #   Column      Non-Null Count   Dtype 
---  ------      --------------   ----- 
 0   podcast_id  150785 non-null  object
 1   title       150785 non-null  object
dtypes: object(2)
memory usage: 2.3+ MB


In [74]:
df_podcast_table.to_csv('df_podcast_table.csv')

In [75]:
df_authors.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 126622 entries, 0 to 126621
Data columns (total 2 columns):
 #   Column          Non-Null Count   Dtype 
---  ------          --------------   ----- 
 0   author_cleaned  126622 non-null  object
 1   author_id       126622 non-null  int64 
dtypes: int64(1), object(1)
memory usage: 1.9+ MB


In [76]:
# rinominiamo la colonna author_cleaned in author_name
df_authors = df_authors.rename(columns={'author_cleaned': 'author_name'})
df_authors = df_authors[['author_id', 'author_name']]

In [77]:
# controlliamo se ci sono stringhe vuote nella colonna author_name
stringhe_vuote = df_authors[df_authors['author_name'] == '']
stringhe_vuote

author_id author_name
82         83

In [78]:
# sistemiamo l'unicio valore che ha stringa vuota con quello corretto
df_authors.loc[df_authors['author_id'] == 83, 'author_name'] = 'Lucy Lawless'

riga = df_authors[df_authors['author_id'] == 83]
riga

author_id   author_name
82         83  Lucy Lawless

In [79]:
duplicati = df_authors[df_authors.duplicated(subset='author_id', keep=False)]

# Visualizza i duplicati trovati
if not duplicati.empty:
    print("ID duplicati trovati:")
    print(duplicati)
else:
    print("Non ci sono ID duplicati.")

Non ci sono ID duplicati.


In [80]:
df_authors.to_csv('authors.csv', index=False)

In [81]:
df_author_podcast.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 157818 entries, 0 to 157817
Data columns (total 2 columns):
 #   Column      Non-Null Count   Dtype 
---  ------      --------------   ----- 
 0   podcast_id  157818 non-null  object
 1   author_id   157818 non-null  int64 
dtypes: int64(1), object(1)
memory usage: 2.4+ MB


In [82]:
df_author_podcast.to_csv('authors_podcast.csv', index=False)

In [83]:
df_dettagli_podcast.head()

podcast_id  \
0  f201172864310534ae6b6c4f8ae9b8cc   
1  6c476d3dd90c3fe5381153354b326952   
2  3cfef94cfccf27eb504bd7a6c7459636   
3  2f2205dcc248024b0a3be4665f38e33a   
4  9fc35a81647e391f93211b5d11973c83   

                                          itunes_url  \
0  https://podcasts.apple.com/us/podcast/rahdo-ta...   
1  https://podcasts.apple.com/us/podcast/idiotspe...   
2  https://podcasts.apple.com/us/podcast/original...   
3  https://podcasts.apple.com/us/podcast/the-big-...   
4  https://podcasts.apple.com/us/podcast/galaktac...   

                                         description  average_rating  \
0  Richard "Rahdo" Ham talks (at great length) al...             4.6   
1                          Podcast by IdiotSpeakShow             NaN   
2  OriginALL este un show cu oameni inteligenti p...             3.7   
3  Much bigger than sports, the show is fun, topi...             4.6   
4  The name Galaktacus originates from a youthful...             5.0   

   ratings_count itunes_img  
0             60             
1           <NA>             
2              3             
3           1300             
4             20

## Data Extraction tramite API iTunes

### Preparazione dataset per scraping immagini podcast

Prepariamo adesso la tabella `dettagli_podcast` aggiungendo la colonna delle immagini di copertina dei podcast e recuperandole tramite una **richiesta API** ad iTunes.

A causa delle limitazioni di richieste al server da parte di Apple (si possono effettuare al massimo 20 richieste al minuto), per evitare di essere bloccati abbiamo deciso di dividere il dataset in 4 parti così da poter spartirci il lavoro e velocizzare il processo:

In [84]:
## librerie
import pandas as pd
import numpy as np

# creazione delle quattro parti del dataframe df_dettagli_podcast
num_parts = 4
df_parts = np.array_split(df_dettagli_podcast, num_parts)

# salvataggio di ciascuna parte in un file CSV
for i, df_part in enumerate(df_parts):
    df_part.to_csv(f'df_dettagli_podcast_part_{i+1}.csv', index=False)

c:\Users\aless\anaconda3\Lib\site-packages\numpy\core\fromnumeric.py:59: FutureWarning: 'DataFrame.swapaxes' is deprecated and will be removed in a future version. Please use 'DataFrame.transpose' instead.
  return bound(*args, **kwds)


### Script per il recupero delle immagini da iTunes

Abbiamo implementato quindi uno script Python per l'estrazione e l'inserimento delle immagini nella colonna `itunes_img` della tabella `dettagli_podcast`.

Utilizzando una parte del DataFrame `dettagli_podcast` alla volta e usando la libreria `requests`, tramite la funzione `get_podcast_image()` facciamo una richiesta API al server di iTunes usando l'URL necessario per recuperare le immagini.  
Per impostare i limiti di richiesta, abbiamo utilizzato le funzioni `limits` e `sleep_and_retry` dalla libreria `ratelimit`.  

Con la funzione `save_progress()`, dopo la creazione del nuovo file CSV temporaneo relativo ai dettagli, ogni 100 immagini trovate questo CSV si aggiorna con i nuovi dati e viene salvato, fino a che lo scraping non è completato e viene salvato il file finale.

Usiamo inoltre la libreria `tqdm` per monitorare il progresso dello script.

In [85]:
import requests
import re
from ratelimit import limits, sleep_and_retry
from tqdm import tqdm

# decommentate e caricate il file csv che avete tra questi
#df_part_1 = pd.read_csv('df_dettagli_podcast_part_1.csv')
df_part_2 = pd.read_csv('df_dettagli_podcast_part_2.csv')
#df_part_3 = pd.read_csv('df_dettagli_podcast_part_3.csv')
#df_part_4 = pd.read_csv('df_dettagli_podcast_part_4.csv')


RATE_LIMIT = 20
PERIOD = 60
SAVE_INTERVAL = 100  # salva ogni 100 elementi

# cast esplicito della colonna itunes_img a object (stringa)
df_part_2['itunes_img'] = df_part_2['itunes_img'].astype('object')

@sleep_and_retry
@limits(calls=RATE_LIMIT, period=PERIOD)
def get_podcast_image(itunes_url):
    try:
        match = re.search(r'id(\d+)', itunes_url)
        if not match:
            raise ValueError("Invalid iTunes URL")

        podcast_id = match.group(1)

        api_url = f"https://itunes.apple.com/lookup?id={podcast_id}"

        response = requests.get(api_url)
        response.raise_for_status()

        data = response.json()
        if data['resultCount'] > 0:
            image_url = data['results'][0]['artworkUrl600']
            return image_url
        else:
            return None
    except Exception as e:
        print(f"Error with URL {itunes_url}: {e}")
        return None

def save_progress(df, start_index, end_index, filename='df_dettagli_podcast_part_2_con_img.csv'):
    temp_df = df.iloc[start_index:end_index]
    if start_index == 0:
        temp_df.to_csv(filename, mode='w', index=False, encoding='utf-8')
    else:
        temp_df.to_csv(filename, mode='a', header=False, index=False, encoding='utf-8')

total_rows = len(df_part_2)

# utilizzo di tqdm per visualizzare la barra di avanzamento
with tqdm(total=total_rows, unit='row') as pbar:
    for start in range(0, total_rows, SAVE_INTERVAL):
        end = min(start + SAVE_INTERVAL, total_rows)
        for idx in range(start, end):
            # assegnazione dei valori convertiti in stringa
            df_part_2.at[idx, 'itunes_img'] = str(get_podcast_image(df_part_2.at[idx, 'itunes_url']))
            pbar.update(1)  # aggiornamento della barra di avanzamento
        save_progress(df_part_2, start, end)

# salvataggio del df finale con le immagini aggiornate
save_progress(df_part_2, 0, total_rows)  # assicura che l'ultimo batch venga salvato

  0%|          | 4/37696 [00:08<22:55:13,  2.19s/row]


KeyboardInterrupt: 

### Ricostruzione csv completo dei dettagli podcast

Una volta terminati i 4 processi, abbiamo ricostruito la tabella completa `dettagli_podcast` concatenando i 4 csv ottenuti:

In [87]:
import pandas as pd

df_originale = pd.read_csv('df_dettagli_podcast.csv')

df1 = pd.read_csv('df_dettagli_podcast_part_1_con_img.csv')
df2 = pd.read_csv('df_dettagli_podcast_part_2_con_img.csv')
df3 = pd.read_csv('df_dettagli_podcast_part_3_con_img.csv')
df4 = pd.read_csv('df_dettagli_podcast_part_4_con_img.csv')

# concatenazione dei 4 df temporanei
df_temporaneo = pd.concat([df1, df2, df3, df4])

# troviamo gli ID mancanti utilizzando la differenza di insiemi con set
ids_presenti = set(df_temporaneo['podcast_id'])
ids_totali = set(df_originale['podcast_id'])
ids_mancanti = ids_totali - ids_presenti

# filtriamo il df originale per ottenere le righe con gli ID mancanti
id_mancanti_df = df_originale[df_originale['podcast_id'].isin(ids_mancanti)]

# aggiungiamo le righe mancanti al df temporaneo
df_completo = pd.concat([df_temporaneo, id_mancanti_df])

# aggiunta immagine di default per podcast senza copertina
df_completo['itunes_img'] = df_completo['itunes_img'].fillna('https://i.postimg.cc/pXmVcV3Q/Image20240529174317.jpg')

# sistemiamo le colonne 'ratings_count' e 'average_rating'
df_completo['ratings_count'].fillna(0, inplace=True)
df_completo['average_rating'] = df_completo['average_rating'].astype('float32')
df_completo['ratings_count'] = df_completo['ratings_count'].astype('int32')

df_completo.to_csv('df_dettagli_podcast_finale.csv', index=False)

C:\Users\aless\AppData\Local\Temp\ipykernel_21116\2958604917.py:28: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df_completo['ratings_count'].fillna(0, inplace=True)


## Categories JSON Cleaning and Transformation

In questa seconda parte, caricheremo il file json relativo ai dati sulle **categorie** e procederemo con i vari step. Nella seguente cella importiamo le librerie necessarie e le funzioni per la data cleaning di questo file.

In [88]:
## librerie
import pandas as pd


# funzione per estrarre la categoria generale
def general_category(category_name):
    return category_name.split('-')[0]

Leggiamo il file csv realtivo alla tabella podcast precedentemente pulita e filtriamo il file delle categorie in base ai `podcast_id` rimasti:

In [89]:
df_podcast_table = pd.read_csv('df_podcast_table.csv')

# set per ricerca più rapida
podcast_ids_set = set(df_podcast_table['podcast_id'])

df_categories = pd.read_json('categories.json', lines=True)

# filtro i dati in base ai podcast_id e tengo solo le righe che servono
df_filtered = df_categories[df_categories['podcast_id'].isin(podcast_ids_set)].copy()

Applichiamo la funzione **general_category** per estrarre la categoria generale:

In [90]:
# applico la funzione
df_filtered['category'] = df_filtered['category'].apply(general_category)

### Creazione tabelle utili e trasformazione in file csv

Lavorando con il df_filtered e il df_podcast_table, creiamo infine i file **categories.csv** e **podcast.csv** finali da poter inserire nel nostro database:

In [91]:
# creo df delle categorie generali uniche e aggiungo categoria unknown, poi cast a int
df_general_categories = df_filtered[['category']].drop_duplicates().reset_index(drop=True)
df_general_categories.loc[len(df_general_categories)] = ['unknown']
df_general_categories['category_id'] = range(1, len(df_general_categories) + 1)
df_general_categories['category_id'] = df_general_categories['category_id'].astype(int)

# unione del df delle categorie generali con il df filtrato per ottenere i category_id
df_filtered = df_filtered.merge(df_general_categories, on='category', how='left')

# assegno una sola categoria principale per ogni podcast_id (prendendo la prima occorrenza)
df_categories_final = df_filtered.drop_duplicates(subset='podcast_id', keep='first')
df_categories_final = df_categories_final[['podcast_id', 'category_id']]

# unisco il df podcast-categorie (df_categories_final) con il df dei podcast così da avere
# la colonna category id corretta nel df dei podcast originale
df_podcast_table = df_podcast_table.merge(df_categories_final, on='podcast_id', how='left')

# Assegna category_id 26 ai podcast senza categoria e cast a int
df_podcast_table['category_id'] = df_podcast_table['category_id'].fillna(26).astype(int)

# cambio la colonna true in true crime e riordino il df
df_general_categories['category'] = df_general_categories['category'].replace('true', 'true crime')
df_general_categories = df_general_categories[['category_id', 'category']]

df_general_categories.to_csv('categories.csv', index=False)

# droppo la colonna unnamed
df_podcast_table = df_podcast_table.drop(columns=['Unnamed: 0'], errors='ignore')

# sistemo il titolo di un podcast
df_podcast_table['title'] = df_podcast_table['title'].fillna('N-A')


df_podcast_table.to_csv('podcast.csv', index=False)

## Reviews JSON Cleaning and Transformation

Infine, ci occupiamo del file **reviews**.  
Data il peso del file (circa 2gb), per evitare di esaurire la memoria, in questo caso usiamo la libreria `json`, insieme a `pandas` e `csv` per leggerlo e poi ottenere il file da inserire nel database. Questo approccio ci permetterà di gestire il caricamento e la trasformazione dei dati in modo più efficiente

In [92]:
## librerie

import pandas as pd
import json
import csv

In [95]:
df_podcast_table = pd.read_csv('df_podcast_table.csv')

# faccio il set degli id poiché la ricerca su un set è più veloce rispetto a una lista
podcast_ids_set = set(df_podcast_table['podcast_id'])

input_file = 'reviews.json'
output_file = 'reviews.csv'

# colonne da ignorare
columns_to_ignore = {'author_id', 'created_at'}

# lettura del file JSON riga per riga e scrittura dei record filtrati in file CSV
with open(input_file, 'r', encoding='utf-8') as infile, open(output_file, 'w', newline='', encoding='utf-8') as csvfile:

    csvwriter = None

    for line in infile:
        try:
            # carico ogni riga come un record JSON
            record = json.loads(line)
            # verifico se il podcast_id è nel set
            if record.get('podcast_id') in podcast_ids_set:
                # rimuovo le colonne da escludere
                for column in columns_to_ignore:
                    record.pop(column, None)
                if csvwriter is None:
                    # inizializzo il csvwriter con le chiavi del primo record filtrato
                    csvwriter = csv.DictWriter(csvfile, fieldnames=record.keys())
                    csvwriter.writeheader()
                # adesso scrivo il record nel file CSV
                csvwriter.writerow(record)
        except json.JSONDecodeError:
            continue

print("File CSV creato con i record filtrati.")

File CSV creato con i record filtrati.


### Extra: Aggiunta di una colonna apposita al file per costruire grafico Word Cloud su PowerBi



In questa parte abbiamo deciso di implementare uno script per creare in seguito il grafico **Word Cloud** su **PowerBi** in cui mostriamo le parole più usate nelle recensioni dei podcast.

In [98]:
import pandas as pd
from wordcloud import STOPWORDS
import re

recensioni = pd.read_csv('reviews.csv')

# Lista di stopwords spagnole
stopwords_spagnole = [
    "de", "la", "que", "el", "en", "y", "a", "los", "del", "se", "las", "por", "un", "para", "con",
    "no", "una", "su", "al", "lo", "como", "más", "pero", "sus", "le", "ya", "o", "este", "sí", "porque",
    "esta", "entre", "cuando", "muy", "sin", "sobre", "también", "me", "hasta", "hay", "donde", "quien",
    "desde", "todo", "nos", "durante", "todos", "uno", "les", "ni", "contra", "otros", "ese", "eso",
    "ante", "ellos", "e", "esto", "mí", "antes", "algunos", "qué", "unos", "yo", "otro", "otras", "otra",
    "él", "tanto", "esa", "estos", "mucho", "quienes", "nada", "muchos", "cual", "poco", "ella", "estar",
    "estas", "algunas", "algo", "nosotros", "mi", "mis", "tú", "te", "ti", "tu", "tus", "ellas", "nosotras",
    "vosotros", "vosotras", "os", "mío", "mía", "míos", "mías", "tuyo", "tuya", "tuyos", "tuyas", "suyo",
    "suya", "suyos", "suyas", "nuestro", "nuestra", "nuestros", "nuestras", "vuestro", "vuestra", "vuestros",
    "vuestras", "esos", "esas", "estoy", "estás", "está", "estamos", "estáis", "están", "esté", "estés",
    "estemos", "estéis", "estén", "estaré", "estarás", "estará", "estaremos", "estaréis", "estarán",
    "estaría", "estarías", "estaríamos", "estaríais", "estarían", "estaba", "estabas", "estábamos",
    "estabais", "estaban", "estuve", "estuviste", "estuvo", "estuvimos", "estuvisteis", "estuvieron",
    "estuviera", "estuvieras", "estuviéramos", "estuvierais", "estuvieran", "estuviese", "estuvieses",
    "estuviésemos", "estuvieseis", "estuviesen", "estando", "estado", "estada", "estados", "estadas",
    "estad"
]

# combinazione delle stopwords inglesi e spagnole
stopwords = set(STOPWORDS).union(stopwords_spagnole)

# funzione per rimuovere la punteggiatura
def remove_punctuation(text):
    return re.sub(r'[^\w\s]', '', text)

# funzione per rimuovere le stopwords e la punteggiatura
def clean_text(text):
    text = text.lower()
    text = remove_punctuation(text)
    return " ".join(word.strip() for word in text.split() if word not in stopwords)

# funzione applicata al contenuto delle recensioni
recensioni['clean_content'] = recensioni['content'].apply(clean_text)

recensioni.to_csv("recensioni_clean_content.csv", index=False)